<a href="https://colab.research.google.com/github/basel5621/final-depi-project/blob/main/Cleaning_dataset1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Load dataset

In [ ]:
# IMPORTANT: RUN THIS CELL IN ORDER TO IMPORT YOUR KAGGLE DATA SOURCES
# TO THE CORRECT LOCATION (/kaggle/input) IN YOUR NOTEBOOK,
# THEN FEEL FREE TO DELETE THIS CELL.
# NOTE: THIS NOTEBOOK ENVIRONMENT DIFFERS FROM KAGGLE'S PYTHON
# ENVIRONMENT SO THERE MAY BE MISSING LIBRARIES USED BY YOUR
# NOTEBOOK.

import os
import sys
from tempfile import NamedTemporaryFile
from urllib.request import urlopen
from urllib.parse import unquote, urlparse
from urllib.error import HTTPError
from zipfile import ZipFile
import tarfile
import shutil

CHUNK_SIZE = 40960
DATA_SOURCE_MAPPING = 'sentiment-dataset-with-1-million-tweets:https%3A%2F%2Fstorage.googleapis.com%2Fkaggle-data-sets%2F2540469%2F4312966%2Fbundle%2Farchive.zip%3FX-Goog-Algorithm%3DGOOG4-RSA-SHA256%26X-Goog-Credential%3Dgcp-kaggle-com%2540kaggle-161607.iam.gserviceaccount.com%252F20241007%252Fauto%252Fstorage%252Fgoog4_request%26X-Goog-Date%3D20241007T200505Z%26X-Goog-Expires%3D259200%26X-Goog-SignedHeaders%3Dhost%26X-Goog-Signature%3D2df62563213dccd0bfc490908245fec339b3d1d5bfbb4ccbf87c8b382de7854c11f4a6bdf9e772b33fb846d761803074e8e55510f4fbb41628d579a7551871df08c34c73a0a60ee9dd047a4a23c21a6fd34e520c81f51efc64e1f26fdbb7b1d7e43cbc64d1b3ca9f71c72911309f96dc9e9acc89096ea33af14ebbc1e02ebe07f52f3d0a2a33a54a02f7a19ce4576968d35e7ed8f3b5213f4caee3b95be3aaa4cd9243561b45dd275382ee4c77e13526695cf0c3dca8349c5a1e4f180fe715e1344a02121a9b04f7ec4ec9516d0ba69caf334593756977bc5ae660f1d69f3729f110d2dbf744d9add8f1b54bb6dde60f5e24d451b049bf6a7aa18cfaa0dd3150'

KAGGLE_INPUT_PATH='/kaggle/input'
KAGGLE_WORKING_PATH='/kaggle/working'
KAGGLE_SYMLINK='kaggle'

!umount /kaggle/input/ 2> /dev/null
shutil.rmtree('/kaggle/input', ignore_errors=True)
os.makedirs(KAGGLE_INPUT_PATH, 0o777, exist_ok=True)
os.makedirs(KAGGLE_WORKING_PATH, 0o777, exist_ok=True)

try:
  os.symlink(KAGGLE_INPUT_PATH, os.path.join("..", 'input'), target_is_directory=True)
except FileExistsError:
  pass
try:
  os.symlink(KAGGLE_WORKING_PATH, os.path.join("..", 'working'), target_is_directory=True)
except FileExistsError:
  pass

for data_source_mapping in DATA_SOURCE_MAPPING.split(','):
    directory, download_url_encoded = data_source_mapping.split(':')
    download_url = unquote(download_url_encoded)
    filename = urlparse(download_url).path
    destination_path = os.path.join(KAGGLE_INPUT_PATH, directory)
    try:
        with urlopen(download_url) as fileres, NamedTemporaryFile() as tfile:
            total_length = fileres.headers['content-length']
            print(f'Downloading {directory}, {total_length} bytes compressed')
            dl = 0
            data = fileres.read(CHUNK_SIZE)
            while len(data) > 0:
                dl += len(data)
                tfile.write(data)
                done = int(50 * dl / int(total_length))
                sys.stdout.write(f"\r[{'=' * done}{' ' * (50-done)}] {dl} bytes downloaded")
                sys.stdout.flush()
                data = fileres.read(CHUNK_SIZE)
            if filename.endswith('.zip'):
              with ZipFile(tfile) as zfile:
                zfile.extractall(destination_path)
            else:
              with tarfile.open(tfile.name) as tarfile:
                tarfile.extractall(destination_path)
            print(f'\nDownloaded and uncompressed: {directory}')
    except HTTPError as e:
        print(f'Failed to load (likely expired) {download_url} to path {destination_path}')
        continue
    except OSError as e:
        print(f'Failed to load {download_url} to path {destination_path}')
        continue

print('Data source import complete.')


[==================================================] 79055816 bytes downloaded
Downloaded and uncompressed: sentiment-dataset-with-1-million-tweets
Data source import complete.


In [ ]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        os.path.join(dirname, filename)
print('done')
# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All"
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

done


In [ ]:
df= pd.read_csv('/kaggle/input/sentiment-dataset-with-1-million-tweets/dataset.csv')

In [ ]:
df.head()

Text Language      Label
0  @Charlie_Corley @Kristine1G @amyklobuchar @Sty...       en  litigious
1  #BadBunny: Como dos gotas de agua: Joven se di...       es   negative
2  https://t.co/YJNiO0p1JV Flagstar Bank disclose...       en  litigious
3  Rwanda is set to host the headquarters of Unit...       en   positive
4  OOPS. I typed her name incorrectly (today’s br...       en  litigious

# Data Cleaning

In [ ]:
df_en=df[df['Language']=='en']

In [ ]:
df.shape,df_en.shape

((937854, 3), (871310, 3))

In [ ]:
dataset=df_en.drop(columns='Language')
dataset.sample()

Text     Label
175347  What the fuck is wrong with him https://t.co/6...  negative

In [ ]:
dataset.Label.unique()

array(['litigious', 'positive', 'negative', 'uncertainty'], dtype=object)

In [ ]:
dataset['label'] = dataset['Label'].map({"negative":0, "positive": 1.0 })
dataset.Label.unique()

array(['litigious', 'positive', 'negative', 'uncertainty'], dtype=object)

In [ ]:
dataset.dropna(inplace=True)
dataset.label.unique()

array([1., 0.])

In [ ]:
dataset.drop_duplicates(inplace=True)

In [ ]:
dataset.shape

(490393, 3)

In [ ]:
dataset.head()

Text     Label  label
3   Rwanda is set to host the headquarters of Unit...  positive    1.0
5   It sucks for me since I'm focused on the natur...  negative    0.0
8   Social Security. Constant political crises dis...  negative    0.0
9   @FilmThePoliceLA A broken rib can puncture a l...  negative    0.0
10  @jacobringenwald @aKeithWatts @CountDankulaTV ...  negative    0.0

In [ ]:
import plotly.express as px
fig = px.pie(dataset, names='Label', title ='Pie chart of different sentiments of tweets')
fig.show()

## get tags and mentions (in case we need them)

In [ ]:
import re
def extract_mentions(text):
    mentions = re.findall(r'@\w+', text)

    return mentions

dataset['mentions'] = dataset['Text'].apply(extract_mentions)

In [ ]:
def extract_Tags(text):
    URLs = re.findall(r'#\w+', text)

    return URLs

dataset['tags'] = dataset['Text'].apply(extract_Tags)

In [ ]:
dataset.head(10)

Text     Label  label  \
3   Rwanda is set to host the headquarters of Unit...  positive    1.0   
5   It sucks for me since I'm focused on the natur...  negative    0.0   
8   Social Security. Constant political crises dis...  negative    0.0   
9   @FilmThePoliceLA A broken rib can puncture a l...  negative    0.0   
10  @jacobringenwald @aKeithWatts @CountDankulaTV ...  negative    0.0   
11  @NZ_HK_SU @telebusiness My question was rhetor...  negative    0.0   
12  Wimbledon: Nick Kyrgios admits spitting toward...  positive    1.0   
13  is booktwt a thing? if so thats her and she sp...  positive    1.0   
16  @roipaee @joe98100959 @Formula1game @redbullra...  negative    0.0   
17  🤩 Power back on (1855749):  North VI in Ladysm...  negative    0.0   

                                             mentions  \
3                                                  []   
5                                                  []   
8                                                  []   
9                                  [@FilmThePoliceLA]   
10  [@jacobringenwald, @aKeithWatts, @CountDankulaTV]   
11                         [@NZ_HK_SU, @telebusiness]   
12                                                 []   
13                                                 []   
16  [@roipaee, @joe98100959, @Formula1game, @redbu...   
17                                                 []   

                                                 tags  
3   [#SovereignGroup, #SovereignAfrica, #UNDP, #Rw...  
5                                                  []  
8                                                  []  
9                                                  []  
10                                                 []  
11                                                 []  
12                                         [#kyrgios]  
13                                                 []  
16                                                 []  
17  [#bchydro, #britishcolumbia, #canada, #powerou...

# Data Preprocessing

In [ ]:
! pip install emoji

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 586.9/586.9 kB 17.8 MB/s eta 0:00:00


In [ ]:
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
import nltk
import emoji
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


True

In [ ]:
def clean_tweet(tweet):
    tweet = re.sub(r'http\S+', '', tweet)  # Remove URLs
    tweet = re.sub(r'@\w+', '', tweet)     # Remove mentions
    tweet = re.sub(r'#\w+', '', tweet)     # Remove tags
    tweet = re.sub(r'[^\w\s]', '', tweet)  # Remove punctuation
    tweet = emoji.replace_emoji(tweet, replace='') #remove emoji
    tweet = tweet.lower()                  # Convert to lowercase
    return tweet

dataset['cleaned_text'] = dataset['Text'].apply(clean_tweet)

In [ ]:
dataset.head(10)

Text     Label  label  \
3   Rwanda is set to host the headquarters of Unit...  positive    1.0   
5   It sucks for me since I'm focused on the natur...  negative    0.0   
8   Social Security. Constant political crises dis...  negative    0.0   
9   @FilmThePoliceLA A broken rib can puncture a l...  negative    0.0   
10  @jacobringenwald @aKeithWatts @CountDankulaTV ...  negative    0.0   
11  @NZ_HK_SU @telebusiness My question was rhetor...  negative    0.0   
12  Wimbledon: Nick Kyrgios admits spitting toward...  positive    1.0   
13  is booktwt a thing? if so thats her and she sp...  positive    1.0   
16  @roipaee @joe98100959 @Formula1game @redbullra...  negative    0.0   
17  🤩 Power back on (1855749):  North VI in Ladysm...  negative    0.0   

                                             mentions  \
3                                                  []   
5                                                  []   
8                                                  []   
9                                  [@FilmThePoliceLA]   
10  [@jacobringenwald, @aKeithWatts, @CountDankulaTV]   
11                         [@NZ_HK_SU, @telebusiness]   
12                                                 []   
13                                                 []   
16  [@roipaee, @joe98100959, @Formula1game, @redbu...   
17                                                 []   

                                                 tags  \
3   [#SovereignGroup, #SovereignAfrica, #UNDP, #Rw...   
5                                                  []   
8                                                  []   
9                                                  []   
10                                                 []   
11                                                 []   
12                                         [#kyrgios]   
13                                                 []   
16                                                 []   
17  [#bchydro, #britishcolumbia, #canada, #powerou...   

                                         cleaned_text  
3   rwanda is set to host the headquarters of unit...  
5   it sucks for me since im focused on the nature...  
8   social security constant political crises dist...  
9    a broken rib can puncture a lung or lead to a...  
10     i agree its a flawed response for a small  ...  
11    my question was rhetorical we all know russi...  
12  wimbledon nick kyrgios admits spitting towards...  
13  is booktwt a thing if so thats her and she spe...  
16       i wrote to them nowwaiting for a response...  
17   power back on 1855749  north vi in ladysmith ...

In [ ]:
stop_words=stopwords.words('english')
stop_words.remove('not')
def pre_processing(text):
  token= word_tokenize(text)

  filtered_token= [word for word in token if word not in stop_words]

  lemmatizer= WordNetLemmatizer()
  filtered_token_after_lemm= [lemmatizer.lemmatize(word) for word in filtered_token]
  return ' '.join(filtered_token_after_lemm)

print("original:\t\t"+dataset['cleaned_text'][10])
print("after preprocessing:\t"+pre_processing(dataset['cleaned_text'][10]))

original:		   i agree its a flawed response for a small  and many pl people i presume would agree that nuance amp understanding is needed in those cases

but its a good starting point  dont drink amp drive or dont play with guns is sound advice that sounds simplistic but nevertheless true
after preprocessing:	agree flawed response small many pl people presume would agree nuance amp understanding needed case good starting point dont drink amp drive dont play gun sound advice sound simplistic nevertheless true


In [ ]:
dataset['cleaned_text']=dataset['cleaned_text'].apply(pre_processing)

## Prepare cleaned data ready for analysis

In [ ]:
df_analysis = dataset[['cleaned_text','label','mentions','tags']]

In [ ]:
df_analysis.reset_index(drop=True,inplace=True)
df_analysis.head()

cleaned_text  label  \
0  rwanda set host headquarters united nation dev...    1.0   
1  suck since im focused nature aspect thing envi...    0.0   
2  social security constant political crisis dist...    0.0   
3  broken rib puncture lung lead collapsed lung m...    0.0   
4  agree flawed response small many pl people pre...    0.0   

                                            mentions  \
0                                                 []   
1                                                 []   
2                                                 []   
3                                 [@FilmThePoliceLA]   
4  [@jacobringenwald, @aKeithWatts, @CountDankulaTV]   

                                                tags  
0  [#SovereignGroup, #SovereignAfrica, #UNDP, #Rw...  
1                                                 []  
2                                                 []  
3                                                 []  
4                                                 []

# save analysis dataset

In [ ]:
df_analysis.to_csv('analysis.csv',index=False)

## Prepare cleaned data ready for training

In [ ]:
trained_df = dataset[['cleaned_text','label']]

In [ ]:
trained_df.head()

cleaned_text  label
3   rwanda set host headquarters united nation dev...    1.0
5   suck since im focused nature aspect thing envi...    0.0
8   social security constant political crisis dist...    0.0
9   broken rib puncture lung lead collapsed lung m...    0.0
10  agree flawed response small many pl people pre...    0.0

## Split the dataset into train and test

In [ ]:
from sklearn.model_selection import train_test_split
df_train, df_test  = train_test_split(trained_df , test_size=0.1, random_state=7,shuffle=True)

print("Train data size ",df_train.shape[0])
print("Test data size ",df_test.shape[0])

Train data size  441353
Test data size  49040


In [ ]:
df_train.reset_index(drop=True,inplace=True)
df_test.reset_index(drop=True,inplace=True)
df_train.head()

cleaned_text  label
0  already tested blood 1947 long game ethnic cle...    1.0
1                                 yep thats hate bad    0.0
2                                              dream    1.0
3  uk first past post electoral system broken lea...    0.0
4  excited welcome one newest member team michell...    1.0

In [ ]:
df_train.shape

(441353, 2)

# save cleaned dataset

In [ ]:
df_train.to_csv('train.csv',index=False)

In [ ]:
df_test.to_csv('test.csv',index=False)